In [1]:
import pandas as pd
import matplotlib as mpl
import plotly.express as px
import numpy as np
import datapane as dp
import altair as alt

In [2]:
df = pd.read_csv ("goldcopyhalfstats.csv")
df.head()

year       game_code                                        a_team_name  \
0  2008   5068820080906  Syracuse                                      ...   
1  2008   8014720080830  Clemson                                       ...   
2  2010   8019320100918  Duke                                          ...   
3  2011  27074220110903  Virginia Tech                                 ...   
4  2011  37014720110917  Clemson                                       ...   

                                   a_name_conference  a_team_code  a_result  \
0  Atlantic Coast Conference                     ...          688         0   
1  Atlantic Coast Conference                     ...          147         0   
2  Atlantic Coast Conference                     ...          193         0   
3  Atlantic Coast Conference                     ...          742         1   
4  Atlantic Coast Conference                     ...          147         1   

   a_points  b_team_code                                          team_name  \
0        14            5  Akron                                         ...   
1         3            8  Alabama                                       ...   
2        13            8  Alabama                                       ...   
3        38           27  Appalachian State                             ...   
4        21           37  Auburn                                        ...   

                                     name_conference  ...  \
0  Mid-American Conference                       ...  ...   
1  Southeastern Conference                       ...  ...   
2  Southeastern Conference                       ...  ...   
3  Southern                                      ...  ...   
4  Southeastern Conference                       ...  ...   

   half_diff_score_abs  visit_date stadium_code  \
0                   14    9/6/2008           92   
1                   17   8/30/2008           38   
2                   29   9/18/2010           80   
3                   38    9/3/2011          136   
4                    0   9/17/2011          112   

                                        stadium_name             site  \
0  Carrier Dome                                  ...  TEAM              
1  Georgia Dome                                  ...  NEUTRAL           
2  Wallace Wade Stadium                          ...  TEAM              
3  Lane Stadium                                  ...  TEAM              
4  Memorial Stadium                              ...  TEAM              

                                                city  state  capacity  \
0  Syracuse                                      ...     NY     49250   
1  Atlanta                                       ...     GA     71250   
2  Durham                                        ...     NC     33941   
3  Blacksburg                                    ...     VA     66233   
4  Clemson                                       ...     SC     86400   

                     surface  year_opened  
0  FieldTurf                         1980  
1  FieldTurf                         1992  
2  Grass                             1929  
3  Grass                             1965  
4  Grass                             1942  

[5 rows x 42 columns]

In [3]:
df.count()

year                    4789
game_code               4789
a_team_name             4789
a_name_conference       4789
a_team_code             4789
a_result                4789
a_points                4789
b_team_code             4789
team_name               4789
name_conference         4789
b_result                4789
b_points                4789
half_leader             4789
a_rush                  4789
b_rush                  4789
a_offense_rush_yards    4789
b_defense_rush_yards    4789
a_defense_rush_yards    4789
b_offense_rush_yards    4789
a_offense_pass_yards    4789
b_defense_pass_yards    4789
a_defense_pass_yards    4789
b_offense_pass_yards    4789
a_pass                  4789
b_pass                  4789
a_incomplete_pass       4789
b_incomplete_pass       4789
a_penalty               4789
b_penalty               4789
a_penalty_yards         4789
b_penalty_yards         4789
half_diff_score         4789
half_diff_score_abs     4789
visit_date              4789
stadium_code  

In [4]:
teamnamelist = df['a_team_name'].tolist()

In [5]:
teamnameofficial=[]
for i in teamnamelist:
    if i not in teamnameofficial:
        teamnameofficial.append(i)
        
teamnameofficial.sort()

In [6]:
#data for dropdown menu by team name
print(teamnameofficial)

['Air Force                                         ', 'Akron                                             ', 'Alabama                                           ', 'Alabama A&M                                       ', 'Alabama St.                                       ', 'Alcorn St.                                        ', 'Appalachian State                                 ', 'Arizona                                           ', 'Arizona State                                     ', 'Arkansas                                          ', 'Arkansas State                                    ', 'Army                                              ', 'Auburn                                            ', 'Austin Peay                                       ', 'BYU                                               ', 'Ball State                                        ', 'Baylor                                            ', 'Bethune-Cookman                                   ', 'Boise State               

In [22]:
#need to find a way to filter by specific conference or team only based on interactive selection
lineplt = px.line(df,
                 x='year',
                 y='a_incomplete_pass',
                 color='a_team_name',
                 hover_name='a_team_name')
menusetup = [
    {'buttons': [
        {
            'method' : 'restyle',
            'label' : 'a_team_name'
        }
    ],
    'direction' : 'down',
    'showactive' : True
    }
]

lineplt = lineplt.update_layout(
            title_text='Points at the Half by Team',
            title_x=0.5,
            #plot_bgcolor= 'rgb(194, 208, 209)',
            xaxis_showgrid=False,
            yaxis_showgrid=False,
            hoverlabel=dict(font_size=10, bgcolor='rgb(69, 95, 154)',
            bordercolor= 'whitesmoke'),
            legend=dict(title='Please click legend item to remove <br>or add to plot',
                        x=0,
                        y=1,
                        traceorder='normal',
                        bgcolor='LightSteelBlue',
                        xanchor = 'auto'),
            updatemenus=menusetup
            )
lineplt = lineplt.update_traces(mode="lines")
lineplt.show()

In [21]:
teamlist = list(df['a_team_name'].unique())
df['year'] = pd.to_datetime(df['year'],format='%Y')
input_dropdown = alt.binding_select(options=teamlist)
selection = alt.selection_single(fields=['a_team_name'], bind=input_dropdown, name='Your Favorite Team')

alt_plot = alt.Chart(df).mark_bar().encode(
    x='year',
    y='a_penalty_yards'
).add_selection(
    selection
).transform_filter(
    selection
)

alt_plot

alt.Chart(...)

In [ ]:
app = dash.Dash(__name__)

#---------------------------------------------------------------
app.layout = html.Div([
    html.Div([
        html.Label(["Your Favorite Team's Stats!"]),
        dcc.Dropdown(
            id='my_dropdown',
            options=[
                     {'label': 'Your Team', 'value': 'a_points'},
                     {'label': 'Opposing Team', 'value': 'b_points'}
            ],
            value='a_points',
            multi=False,
            clearable=False,
            style={"width": "50%"}
        ),
    ]),

    html.Div([
        dcc.Graph(id='the_graph')
    ]),

])

#---------------------------------------------------------------
@app.callback(
    Output(component_id='the_graph', component_property='figure'),
    [Input(component_id='my_dropdown', component_property='value')]
)

def update_graph(my_dropdown):
    dfgraph = df

    piechart=px.pie(
            data_frame=dfgraph,
            names=my_dropdown,
            hole=.0,
            )

    return (piechart)


if __name__ == '__main__':
    app.run_server(debug=True)

In [ ]:
c